# Capstone Project - The Battle of the Neighborhoods

### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)

## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening an **Indian restaurant** in **Toronto**, Canada.

Since there are lots of restaurants in Toronto we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with no Indian restaurants in vicinity**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met. we are using **Nathan Plaza Square** as our city center of Toronto

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.


## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to Indian restaurants in the neighborhood, if any
* distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **Google Maps API reverse geocoding**
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of Toronto center will be obtained using **Google Maps API geocoding** of well known Toronto location (Nathan Plaza Square)

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around Toronto city center.

Let's first find the latitude & longitude of Toronto city center, using specific, well known address and Google Maps geocoding API.

In [0]:
# Google API key has been removed for security purpose

In [52]:
import requests

def get_coordinates(api_key, address, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&address={}'.format(api_key, address)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        geographical_data = results[0]['geometry']['location'] # get geographical coordinates
        lat = geographical_data['lat']
        lon = geographical_data['lng']
        return [lat, lon]
    except:
        return [None, None]
address = 'Nathan Phillips Square, Toronto, CA'
toronto_center = get_coordinates(google_api_key, address)
print('Coordinate of {}: {}'.format(address, toronto_center))


Coordinate of Nathan Phillips Square, Toronto, CA: [43.6527069, -79.38341369999999]


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from Nathan Plaza Square. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [5]:
#!pip install shapely
import shapely.geometry

!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Toronto center longitude={}, latitude={}'.format(toronto_center[1], toronto_center[0]))
x, y = lonlat_to_xy(toronto_center[1], toronto_center[0])
print('Berlin center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Toronto center longitude={}, latitude={}'.format(lo, la))

     |████████████████████████████████| 10.1MB 9.5MB/s 
Coordinate transformation check
-------------------------------
Toronto center longitude=-79.38341369999999, latitude=43.6527069
Berlin center UTM X=-5310657.177355793, Y=10507491.903773136
Toronto center longitude=-79.38341370000047, latitude=43.65270689999976


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [6]:
toronto_center_x, toronto_center_y = lonlat_to_xy(toronto_center[1], toronto_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = toronto_center_x - 6000
x_step = 600
y_min = toronto_center_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(toronto_center_x, toronto_center_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

364 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:




In [0]:
#!pip install folium

import folium

In [8]:
map_toronto = folium.Map(location=toronto_center, zoom_start=13)
folium.Marker(toronto_center, popup='Nathan Phillips Square').add_to(map_toronto)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_toronto) 
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_toronto)
    #folium.Marker([lat, lon]).add_to(map_toronto)
map_toronto

We now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from Nathan Plaza Square. 

Let's now use Google Maps API to get approximate addresses of those locations.

In [10]:
def get_address(api_key, latitude, longitude, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&latlng={},{}'.format(api_key, latitude, longitude)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        address = results[0]['formatted_address']
        return address
    except:
        return None

addr = get_address(google_api_key, toronto_center[0], toronto_center[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(toronto_center[0], toronto_center[1], addr))

Reverse geocoding check
-----------------------
Address of [43.6527069, -79.38341369999999] is: 100 Queen St W, Toronto, ON M5H 2N2, Canada


In [11]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(google_api_key, lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', Toronto', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [12]:
addresses[150:170]

['49 Highland Ave, ON M4W 2A2, Canada',
 '74 Whitehall Rd, ON M4W 2C7, Canada',
 '214 Inglewood Dr, ON M4T 1H9, Canada',
 '16 Avenue of the Island, ON, Canada',
 'Unnamed Road, ON M5J, Canada',
 'Toronto Division, ON, Canada',
 'Toronto Division, ON, Canada',
 'Toronto Division, ON, Canada',
 'Unnamed Road, ON M5J 2G4, Canada',
 '20 Bay St, ON M6J 2N8, Canada',
 'Union Station Bus Terminal, 141 Bay St, ON M5J 1J5, Canada',
 '4 King St W, ON M5H 1A1, Canada',
 '189 Yonge St, ON M5B 2H1, Canada',
 'Heaslip House, ON M5B 1W1, Canada',
 '64 McGill St, ON M5B 1H2, Canada',
 '510 Church St, ON M4Y 2C8, Canada',
 '579 Church St, ON M4Y 2E4, Canada',
 '200 Bloor St E, ON M4W 1E6, Canada',
 '115 Park Rd, ON M4W 2N8, Canada',
 '151 Roxborough St E, ON M4W 1V9, Canada']

###Placing all this into a Pandas dataframe.

In [13]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address  ...  Distance from center
0                      490 Unwin Ave, ON M5A, Canada  ...           5992.495307
1                440 R Unwin Ave, ON M4M 3B9, Canada  ...           5840.376700
2           515 Commissioners St, ON M4M 1A5, Canada  ...           5747.173218
3  10 Lower Don Recreation Trail, ON M4M 1E4, Canada  ...           5715.767665
4               37 Winnifred Ave, ON M4M 2X2, Canada  ...           5747.173218
5               65 Bertmount Ave, ON M4M 2X8, Canada  ...           5840.376700
6                    46 Galt Ave, ON M4M 2Z1, Canada  ...           5992.495307
7                       4 Regatta Rd, ON M5A, Canada  ...           5855.766389
8                  315 Unwin Ave, ON M4M 3M9, Canada  ...           5604.462508
9                    17 Basin St, ON M4M 1A1, Canada  ...           5408.326913

[10 rows x 6 columns]

...and let's now save/persist this data into local file.

In [0]:
df_locations.to_pickle('./locations.pkl')  

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.
​
We're interested in venues in 'food' category, but only those that are proper restaurants - coffe shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in out list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Italian restaurant' category, as we need info on Italian restaurants in the neighborhood.

In [0]:
client_id = 'YNW20B1MZTYJXKUL1EQHSA2LVPOVACEAWAGSTQ0JQKSOH5XB' # your Foursquare ID
client_secret = 'NPX5KHGOF0O2DWNCYTJMCTUT2VOJYVE1HZYVY03T3XJYKPCF' # your Foursquare Secret
version = '20180605' # Foursquare API version

In [0]:
# Category IDs corresponding to Italian restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4bf58dd8d48988d10f941735' # 'Root' category for all food-related venues

indian_restaurant_categories = ['54135bf5e4b08f3d2429dfe5','54135bf5e4b08f3d2429dff3','54135bf5e4b08f3d2429dff5',
                                 '54135bf5e4b08f3d2429dfe2','54135bf5e4b08f3d2429dff2','54135bf5e4b08f3d2429dfe1',
                                 '54135bf5e4b08f3d2429dfe3','54135bf5e4b08f3d2429dfe8','54135bf5e4b08f3d2429dfe9',
                                 '54135bf5e4b08f3d2429dfe6','54135bf5e4b08f3d2429dfdf','54135bf5e4b08f3d2429dfe4',
                                 '54135bf5e4b08f3d2429dfe7','54135bf5e4b08f3d2429dfea','54135bf5e4b08f3d2429dfeb',
                                 '54135bf5e4b08f3d2429dfed','54135bf5e4b08f3d2429dfee','54135bf5e4b08f3d2429dff4',
                                 '54135bf5e4b08f3d2429dfe0','54135bf5e4b08f3d2429dfdd','54135bf5e4b08f3d2429dff6',
                                 '54135bf5e4b08f3d2429dfef','54135bf5e4b08f3d2429dff0','54135bf5e4b08f3d2429dff1',
                                 '54135bf5e4b08f3d2429dfde','54135bf5e4b08f3d2429dfec']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Toronto', '')
    address = address.replace(', Canada', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [17]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found indian restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    indian_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, client_id, client_secret, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_indian = is_restaurant(venue_categories, specific_filter=indian_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_indian, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_indian:
                    indian_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, indian_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
indian_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_350.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('indian_restaurants_350.pkl', 'rb') as f:
        indian_restaurants = pickle.load(f)
    with open('location_restaurants_350.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, indian_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('indian_restaurants_350.pkl', 'wb') as f:
        pickle.dump(indian_restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)

Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [18]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of Indian restaurants:', len(indian_restaurants))
print('Percentage of Indian restaurants: {:.2f}%'.format(len(indian_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 107
Total number of Indian restaurants: 3
Percentage of Indian restaurants: 2.80%
Average number of restaurants in neighborhood: 0.47527472527472525


In [19]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('5c79c06d780eee002cc223ec', 'My Roti Place', 43.660945, -79.341114, '948 Queen st east ON M4M 1J7', 273, False, -5309884.323620845, 10502461.062213404)
('511d3938e4b08cadc4d1e41c', 'Namaste Nepal', 43.67863464355469, -79.34662628173828, 'Toronto ON', 43, False, -5307000.341583881, 10502789.200214647)
('5621af15498e5d8e58025ed7', 'Siddhartha Indian', 43.65911684437622, -79.34894800186157, '734 Queen St E ON M4M 1H2', 316, False, -5310075.989152386, 10503397.920373641)
('5cf9b721e1f228002c408f16', 'Good Karma', 43.658639, -79.350339, '689 Queen St E (Broadview Avenue) ON M4M 1G6', 206, False, -5310134.384264389, 10503566.953711782)
('4b4122f1f964a520ddc125e3', 'Green Earth Vegetarian', 43.66589, -79.35265, '385 Broadview (Gerrard) ON', 121, False, -5308951.408255496, 10503707.214101393)
('4c1d5337eac020a1cb1048c2', 'Sher-E-Punjab', 43.67730788939673, -79.35306551709385, '351 Danforth Ave (at Jackman Ave) ON M4K 1N7', 213, False, -5307129.8

In [20]:
print('List of Indian restaurants')
print('---------------------------')
for r in list(indian_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(indian_restaurants))

List of Indian restaurants
---------------------------
('5ced954086f4cc00360fb502', 'My Roti Place', 43.64172, -79.37581, '12 Queen Quay West ON M5J 2V7', 119, True, -5312502.622456368, 10506806.547392087)
('5d233d7ba18cd500300eb8e3', 'My Dosa Place', 43.64214, -79.37579, '12 Queens Quay W ON M5J 2V7', 122, True, -5312436.036894776, 10506796.852897843)
('5d91774746c430000815ba3e', 'DASHA', 43.6444884, -79.4007969, '620 King St. W. ON M5V 1K4', 318, True, -5311742.2177406205, 10509645.326923577)
...
Total: 3


In [21]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: 
Restaurants around location 102: 
Restaurants around location 103: 
Restaurants around location 104: Tumeric
Restaurants around location 105: Amaya Express
Restaurants around location 106: Al Noor Grill
Restaurants around location 107: Sultan Of Samosas, Al Noor Grill
Restaurants around location 108: 
Restaurants around location 109: Butter Chicken Factory, Rainbow Restaurant
Restaurants around location 110: 


Let's now see all the collected restaurants in our area of interest on map, and let's also show Indian
restaurants in different color.

In [22]:
map_toronto = folium.Map(location=toronto_center, zoom_start=13)
folium.Marker(toronto_center, popup='Nathan plaza square').add_to(map_toronto)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_indian= res[6]
    color = 'red' if is_indian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_toronto)
map_toronto

Now we have all the restaurants in area within few kilometers from Nathan Plaza square, and we know which ones are Indian restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Indian restaurant!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Toronto that have low restaurant density, particularly those with low number of Indian restaurants. We will limit our analysis to area ~6km around city center.

In first step we have collected the required **data: location and type (category) of every restaurant within 6km from Toronto center** (Alexanderplatz). We have also **identified Indian restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**restaurant density**' across different areas of Berlin - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general (*and* no Italian restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**, and we want locations **without Indian restaurants in radius of 400 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in every area candidate**:

In [23]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 0.47527472527472525


Address  ...  Restaurants in area
0                      490 Unwin Ave, ON M5A, Canada  ...                    0
1                440 R Unwin Ave, ON M4M 3B9, Canada  ...                    0
2           515 Commissioners St, ON M4M 1A5, Canada  ...                    0
3  10 Lower Don Recreation Trail, ON M4M 1E4, Canada  ...                    0
4               37 Winnifred Ave, ON M4M 2X2, Canada  ...                    0
5               65 Bertmount Ave, ON M4M 2X8, Canada  ...                    0
6                    46 Galt Ave, ON M4M 2Z1, Canada  ...                    0
7                       4 Regatta Rd, ON M5A, Canada  ...                    0
8                  315 Unwin Ave, ON M4M 3M9, Canada  ...                    0
9                    17 Basin St, ON M4M 1A1, Canada  ...                    0

[10 rows x 7 columns]

OK, now let's calculate the **distance to nearest Indian restaurant from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [0]:
distances_to_indian_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in indian_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_indian_restaurant.append(min_distance)

df_locations['Distance to Indian restaurant'] = distances_to_indian_restaurant

In [25]:
df_locations.head(10)

Address  ...  Distance to Indian restaurant
0                      490 Unwin Ave, ON M5A, Canada  ...                    5020.761297
1                440 R Unwin Ave, ON M4M 3B9, Canada  ...                    5053.976202
2           515 Commissioners St, ON M4M 1A5, Canada  ...                    5157.257691
3  10 Lower Don Recreation Trail, ON M4M 1E4, Canada  ...                    5326.531549
4               37 Winnifred Ave, ON M4M 2X2, Canada  ...                    5555.769055
5               65 Bertmount Ave, ON M4M 2X8, Canada  ...                    5837.910691
6                    46 Galt Ave, ON M4M 2Z1, Canada  ...                    6165.698069
7                       4 Regatta Rd, ON M5A, Canada  ...                    4591.028752
8                  315 Unwin Ave, ON M4M 3M9, Canada  ...                    4512.543223
9                    17 Basin St, ON M4M 1A1, Canada  ...                    4509.731453

[10 rows x 8 columns]

In [26]:
print('Average distance to closest Indian restaurant from each area center:', df_locations['Distance to Indian restaurant'].mean())

Average distance to closest Indian restaurant from each area center: 3517.7153824688994


OK, so **on average Indian restaurant can be found within ~5500m** from every area center candidate. 

Let's crete a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show **borders of toronto boroughs** on our map and a few circles indicating distance of 1km, 2km and 3km from Nathan Plaza Square.

In [0]:
toronto_boroughs_url = 'https://raw.githubusercontent.com/saran4code/toronto_borough/master/simple.geojson'
toronto_boroughs = requests.get(toronto_boroughs_url).json()


def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }


In [0]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

indian_latlons = [[res[2], res[3]] for res in indian_restaurants.values()]

In [30]:
from folium import plugins
from folium.plugins import HeatMap

map_toronto = folium.Map(location=toronto_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_toronto) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_toronto)
folium.Marker(toronto_center).add_to(map_toronto)
folium.Circle(toronto_center, radius=1000, fill=False, color='white').add_to(map_toronto)
folium.Circle(toronto_center, radius=2000, fill=False, color='white').add_to(map_toronto)
folium.Circle(toronto_center, radius=3000, fill=False, color='white').add_to(map_toronto)
folium.GeoJson(toronto_boroughs, style_function=boroughs_style, name='geojson').add_to(map_toronto)
map_toronto

We see low restaurant density closest to city center on North-west and North-east. Let's create another heatmap map showing heatmap/density of Indian restaurants only.

In [31]:
map_toronto = folium.Map(location=toronto_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_toronto) #cartodbpositron cartodbdark_matter
HeatMap(indian_latlons).add_to(map_toronto)
folium.Marker(toronto_center).add_to(map_toronto)
folium.Circle(toronto_center, radius=1000, fill=False, color='white').add_to(map_toronto)
folium.Circle(toronto_center, radius=2000, fill=False, color='white').add_to(map_toronto)
folium.Circle(toronto_center, radius=3000, fill=False, color='white').add_to(map_toronto)
folium.GeoJson(toronto_boroughs, style_function=boroughs_style, name='geojson').add_to(map_toronto)
map_toronto

This map is not so 'hot' (Indian restaurants represent a subset of ~2% of all restaurants in toronto) but it also indicates existing Indian restaurants in South and South-west from Nathan Plaza Square, with closest pockets of **low Indian restaurant density positioned North, North-west from city center**.

Based on this we will now focus our analysis on areas *North, North-west from Toronto center* - we will move the center of our area of interest and reduce it's size to have a radius of **2.5km**. This places our location candidates mostly in boroughs **Kensington Market and Cabbagetown** 

### Kensington Market and Cabbagetown
​
Analysis of popular travel guides and web sites often mention Kensington Market is a cheerful bustle on summer's days, beautiful, interesting, 
rich with culture, cool neighborhood popular among tourists. Both Kensington Market and Cabbagetown are one of Toronto's oldest 
and most diverse neighbourhoods. 


Kensington Market has long been revered for its diverse cultural life and as a part of Toronto. With bars,coffee shops, restaurants, Organic grocery stores, bookstores, vntage clothing stores and all manner of other little oddities. 
The market is as eclectic as the people who live there, The neighborhood is varied, but the music is constant. Each restaurant produces a smell from a different corner of hte world, fusing flavors that have never been put together before. 
The peace and the energy are frenetic. Kensington market has also been a favorite spot for tourists as the locality has cuisines from around the globe. (airbnb)


Cabbagetown is one of the few neighborhoods in Toronto that has really kept the essence of its spirit as the world around it has changed. Most of the stores and restaurants 
are mom and pop stores, giving the whole area a quiet, community feel. Nothing proves the point more than the working farm you can find in the middle of Cabbagetown’s mix of 
Victorian homes and global cuisine. It’s located in Toronto’s East End, so both the Beaches and Downtown Toronto are a short stroll away.  (theculturetrip.com)

In [32]:
roi_x_min = toronto_center_x - 2000
roi_y_max = toronto_center_y + 2000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_toronto= folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_toronto)
folium.Marker(toronto_center).add_to(map_toronto)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_toronto)
folium.GeoJson(toronto_boroughs, style_function=boroughs_style, name='geojson').add_to(map_toronto)
map_toronto

Not bad - this nicely covers all the pockets of low restaurant density in Kensington Market and Cabbage town closest to Nathan Plaza Square.


Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [34]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

2261 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Indianrestaurant**.

In [36]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_indian_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, indian_restaurants)
    roi_indian_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [37]:
#Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Indian restaurant':roi_indian_distances})

df_roi_locations.head(10)

Latitude  Longitude  ...  Restaurants nearby  Distance to Indian restaurant
0  43.657556 -79.358182  ...                   0                    3206.338303
1  43.658177 -79.358276  ...                   0                    3276.641149
2  43.654081 -79.358405  ...                   0                    2782.019216
3  43.654702 -79.358499  ...                   0                    2843.484276
4  43.655323 -79.358593  ...                   0                    2907.090424
5  43.655944 -79.358687  ...                   0                    2972.700228
6  43.656565 -79.358781  ...                   0                    3040.183967
7  43.657186 -79.358876  ...                   0                    3109.419634
8  43.657807 -79.358970  ...                   0                    3180.292811
9  43.658428 -79.359064  ...                   0                    3252.696462

[10 rows x 6 columns]

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no Indian restaurants in radius of 400 meters**.

In [39]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ind_distance = np.array(df_roi_locations['Distance to Indian restaurant']>=400)
print('Locations with no Indian restaurants within 400m:', good_ind_distance.sum())

good_locations = np.logical_and(good_res_count, good_ind_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two restaurants nearby: 2197
Locations with no Indian restaurants within 400m: 2214
Locations with both conditions met: 2156


In [41]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_toronto = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_toronto)
HeatMap(restaurant_latlons).add_to(map_toronto)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_toronto)
folium.Marker(toronto_center).add_to(map_toronto)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_toronto) 
folium.GeoJson(toronto_boroughs, style_function=boroughs_style, name='geojson').add_to(map_toronto)
map_toronto

Looking good. We now have a bunch of locations fairly close to Nathan Plaza Square (mostly in Kensington, CabbageTown), and we know that each of those locations has no more than two restaurants in radius of 250m, and no Indian restaurant closer than 4000m. Any of those locations is a potential candidate for a new Indian restaurant, atleast based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [42]:
map_toronto = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_toronto)
folium.Marker(toronto_center).add_to(map_toronto)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_toronto)
folium.GeoJson(toronto_boroughs, style_function=boroughs_style, name='geojson').add_to(map_toronto)
map_toronto

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Indian restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [43]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_toronto = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_toronto)
HeatMap(restaurant_latlons).add_to(map_toronto)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_toronto)
folium.Marker(toronto_center).add_to(map_toronto)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_toronto) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_toronto)
folium.GeoJson(toronto_boroughs, style_function=boroughs_style, name='geojson').add_to(map_toronto)
map_toronto

Our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.



In [0]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(google_api_key, lat, lon).replace(', Canada', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, toronto_center_x, toronto_center_y)
    print('{}{} => {:.1f}km from Nathan Plaza Square'.format(addr, ' '*(50-len(addr)), d/1000))

Addresses of centers of areas recommended for further analysis

11 King St W, Toronto, ON M5H 4C7                  => 0.9km from Nathan Plaza Square
444 Yonge St, Toronto, ON M5B 2H4                  => 1.3km from Nathan Plaza Square
11 St Bartholomew St, Toronto, ON M5A 1Y5          => 2.5km from Nathan Plaza Square
85 Huron St, Toronto, ON M5T 2A8                   => 1.5km from Nathan Plaza Square
Parliament St at Winchester St, Toronto, ON M4X 1P4 => 2.7km from Nathan Plaza Square
250 Front St E, Toronto, ON M5A 1E9                => 2.3km from Nathan Plaza Square
Teefy Hall, Toronto, ON M5S 2C4                    => 2.3km from Nathan Plaza Square
561 Jarvis St, Toronto, ON M4Y 3B9                 => 2.5km from Nathan Plaza Square
161 Gerrard St E, Toronto, ON M5A 2E4              => 1.7km from Nathan Plaza Square
Union Station, 65 Front St W, Toronto, ON M5J 1E6  => 1.4km from Nathan Plaza Square
21 Lower Jarvis St, Toronto, ON M5E 1R8            => 1.9km from Nathan Plaza Square


This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no Italian restaurants nearby, all zones being fairly close to city center (all less than 3km from Nathan Plaza Square, and about half of those less than 2km from city center). Although zones are shown on map with a radius of ~5000 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located in Kensington Market and CabbageTown boroughs, which we have identified as interesting due to being popular with tourists, fairly close to city center and well connected by public transport.

In [0]:
map_toronto = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(toronto_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_toronto)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_toronto) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_toronto)
map_toronto

## Results and Discussion <a name="results"></a>

Our analysis shows that although there are quite a number of restaurants in Toronto (~350 in our initial area of interest which was 12x12km around Nathan Plaza Square), there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected South and South-west from Nathan Plaza Square, so we focused our attention to areas south, south-east and east, corresponding to boroughs Kensington Market and CabbageTown. 

After directing our attention to this more narrow area of interest (covering approx. 5x5km North-west from Nathan Plaza Square) we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Italian restaurant closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Indian restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Toronto center but not crowded with existing restaurants (particularly Indian) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Toronto areas close to center with low number of restaurants (particularly Indian restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Indian restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis (Kensington Market and CabbageTown), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.